In [1]:
# Importando bibliotecas

from pyspark.sql import *
from pyspark.sql.functions import *
from pyspark.sql.types import *
from datetime import *
from dateutil.relativedelta import relativedelta

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 3, Finished, Available, Finished)

In [2]:
# Formatação do tipo Data 

def log():
  return datetime.now().strftime('%Y-%m-%d %H:%M:%S') + ' >>>'

dt_proc = datetime.now().strftime('%Y%m%d%H%M%S')
current_date = datetime.now().strftime('%Y%m%d')

# Parametrizando a Data do Processamento do book

dt_proc_book = datetime.strptime('2024-02-29', '%Y-%m-%d')
dt_ini_proc_book = dt_proc_book - relativedelta(months=12)

dt_proc_book = dt_proc_book.strftime('%Y%m')
dt_ini_proc_book = dt_ini_proc_book.strftime('%Y%m')

dt_proc_book, dt_ini_proc_book

# Data do Processamento do book em String

dt_proc_book_str = datetime.strptime('2024-02-29', '%Y-%m-%d').strftime('%Y-%m-%d')
dt_proc_book_str

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 4, Finished, Available, Finished)

'2024-02-29'

**Acessando o Arquivo da Tabela Fatura**

In [ ]:
# Leitura dos arquivos Parquet na pasta Trusted tb_fatura

tb_fatura = spark.read.parquet("Files/Trusted/tb_fatura")

tb_fatura.createOrReplaceTempView("tb_fatura")

display(tb_fatura)

In [9]:
tb_fatura.where('id_cliente = 9 and id_fatura = 913').show()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 11, Finished, Available, Finished)

+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+
|id_fatura|id_cliente|       dt_proc|data_emissao_fatura|data_vencimento_fatura|ano_emissao_fatura|valor_fatura|valor_pagamento_minimo|   ref|
+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+
|      913|         9|20250128171726|         2024-01-01|            2024-01-10|              2024|    58474.52|              17542.36|202401|
+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+



In [ ]:
spark.sql("""
            SELECT
                id_fatura,
                id_cliente,
                COUNT(*)
            FROM tb_fatura
            GROUP BY 1,2
            ORDER BY 3 DESC

""").show()

In [12]:
# Criando chave de deduplicação
tb_fatura_dedup = spark.sql("""
            SELECT
            ref  || dt_proc as dedup_key,
              *
            FROM tb_fatura
""")
tb_fatura_dedup.createOrReplaceTempView('tb_fatura_dedup')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 14, Finished, Available, Finished)

In [13]:
#
tb_fatura_dedup_01 = spark.sql("""
            SELECT
                id_fatura,
                id_cliente,
                max(dedup_key) as max_dedup_key
            FROM tb_fatura_dedup
            GROUP BY 1,2
""")
tb_fatura_dedup_01.createOrReplaceTempView('tb_fatura_dedup_01')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 15, Finished, Available, Finished)

In [14]:
tb_fatura_dedup_01.show(1)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 16, Finished, Available, Finished)

+---------+----------+--------------------+
|id_fatura|id_cliente|       max_dedup_key|
+---------+----------+--------------------+
|       11|         1|20230120250128171726|
+---------+----------+--------------------+
only showing top 1 row



In [15]:
# JOIN da tabela principal com a max_dedup

tb_fatura_dedup_02 = spark.sql("""
            SELECT
                a.*

            FROM tb_fatura_dedup a
            LEFT JOIN tb_fatura_dedup_01 b
            ON a.id_fatura = b.id_fatura AND a.id_cliente = b.id_cliente
            WHERE a.dedup_key = b.max_dedup_key
""")
tb_fatura_dedup_02.createOrReplaceTempView('tb_fatura_dedup_02')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 17, Finished, Available, Finished)

In [16]:
tb_fatura_dedup_02.where('id_cliente = 9 and id_fatura = 913').show()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 18, Finished, Available, Finished)

+--------------------+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+
|           dedup_key|id_fatura|id_cliente|       dt_proc|data_emissao_fatura|data_vencimento_fatura|ano_emissao_fatura|valor_fatura|valor_pagamento_minimo|   ref|
+--------------------+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+
|20240120250128171726|      913|         9|20250128171726|         2024-01-01|            2024-01-10|              2024|    58474.52|              17542.36|202401|
+--------------------+---------+----------+--------------+-------------------+----------------------+------------------+------------+----------------------+------+



**Acessando o Arquivo da Tabela Pagamento**

In [18]:
# Leitura  dos arquivos Parquet na pasta Trusted tb_pagamento

tb_pagamento = spark.read.parquet("Files/Trusted/tb_pagamento")

tb_pagamento.createOrReplaceTempView("tb_pagamento")

display(tb_pagamento)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 20, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 6e9feee6-45b8-489b-9e1a-a925b87e4e81)

In [19]:
tb_pagamento.where('id_cliente = 9 and id_fatura = 913').show()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 21, Finished, Available, Finished)

+------------+---------+----------+--------------+--------------+---------------+------+
|id_pagamento|id_fatura|id_cliente|       dt_proc|data_pagamento|valor_pagamento|   Ref|
+------------+---------+----------+--------------+--------------+---------------+------+
|         913|      913|         9|20250128183013|    2024-01-20|       25375.12|202401|
+------------+---------+----------+--------------+--------------+---------------+------+



In [ ]:
# Contagem tabela pagamento

spark.sql("""
            SELECT
                id_fatura,
                id_cliente,
                COUNT(*)
            FROM tb_pagamento
            GROUP BY 1,2
            ORDER BY 3 DESC

""").show()

In [23]:
# Criando chave de deduplicação pagamento

tb_pagamento_dedup = spark.sql("""
            SELECT
            ref  || dt_proc as dedup_key,
              *
            FROM tb_pagamento
""")
tb_pagamento_dedup.createOrReplaceTempView('tb_pagamento_dedup')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 25, Finished, Available, Finished)

In [25]:
#
tb_pagamento_dedup_01 = spark.sql("""
            SELECT
                id_fatura,
                id_cliente,
                max(dedup_key) as max_dedup_key
            FROM tb_pagamento_dedup
            GROUP BY 1,2
""")
tb_pagamento_dedup_01.createOrReplaceTempView('tb_pagamento_dedup_01')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 27, Finished, Available, Finished)

In [26]:
tb_pagamento_dedup_01.show(4)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 28, Finished, Available, Finished)

+---------+----------+--------------------+
|id_fatura|id_cliente|       max_dedup_key|
+---------+----------+--------------------+
|       11|         1|20230120250128183013|
|       12|         1|20230320250128183013|
|       14|         1|20230420250128183013|
|       15|         1|20230520250128183013|
+---------+----------+--------------------+
only showing top 4 rows



In [27]:
# JOIN da tabela principal com a max_dedup - Pagamento

tb_pagamento_dedup_02 = spark.sql("""
            SELECT
                a.*

            FROM tb_pagamento_dedup a
            LEFT JOIN tb_pagamento_dedup_01 b
            ON a.id_fatura = b.id_fatura AND a.id_cliente = b.id_cliente
            WHERE a.dedup_key = b.max_dedup_key
""")
tb_pagamento_dedup_02.createOrReplaceTempView('tb_pagamento_dedup_02')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 29, Finished, Available, Finished)

In [28]:
tb_pagamento_dedup_02.where('id_cliente = 9 and id_fatura = 913').show()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 30, Finished, Available, Finished)

+--------------------+------------+---------+----------+--------------+--------------+---------------+------+
|           dedup_key|id_pagamento|id_fatura|id_cliente|       dt_proc|data_pagamento|valor_pagamento|   Ref|
+--------------------+------------+---------+----------+--------------+--------------+---------------+------+
|20240120250128183013|         913|      913|         9|20250128183013|    2024-01-20|       25375.12|202401|
+--------------------+------------+---------+----------+--------------+--------------+---------------+------+



In [29]:
# Join Tabelas

df_join = spark.sql("""
    SELECT
        a.id_cliente,
        a.id_fatura,
        a.data_emissao_fatura,
        a.data_vencimento_fatura,
        a.valor_fatura,
        a.valor_pagamento_minimo,
        b.id_pagamento,
        b.data_pagamento,
        b.valor_pagamento
    FROM tb_fatura_dedup_02 a
    LEFT JOIN tb_pagamento_dedup_02 b
    ON a.id_fatura = b.id_fatura AND  a.id_cliente = b.id_cliente
    ORDER BY a.id_cliente, a.id_fatura
""")
df_join.createOrReplaceTempView('df_join')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 31, Finished, Available, Finished)

In [30]:
spark.sql("""
      SELECT
          id_cliente,
          id_fatura,
          data_emissao_fatura,
          data_vencimento_fatura,
          valor_fatura,
          valor_pagamento_minimo,
          data_pagamento,
          valor_pagamento
      FROM df_join
""").show(2)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 32, Finished, Available, Finished)

+----------+---------+-------------------+----------------------+------------+----------------------+--------------+---------------+
|id_cliente|id_fatura|data_emissao_fatura|data_vencimento_fatura|valor_fatura|valor_pagamento_minimo|data_pagamento|valor_pagamento|
+----------+---------+-------------------+----------------------+------------+----------------------+--------------+---------------+
|         1|       11|         2023-01-01|            2023-01-10|    24597.21|               7379.16|    2023-01-27|        8944.39|
|         1|       12|         2023-02-01|            2023-02-10|    48891.09|              14667.33|    2023-03-05|       16888.91|
+----------+---------+-------------------+----------------------+------------+----------------------+--------------+---------------+
only showing top 2 rows



In [31]:
# SEM_PAGAMENTO, PAGAMENTO_NO_PRAZO, PAGAMENTO_ANTECIPADO, PAGAMENTO_EM_ATRAZO

tb_classificacao_pagamento = spark.sql("""
    select
        *,
        case
            when data_pagamento is null then 'SEM_PAGAMENTO'
            when data_pagamento = data_vencimento_fatura then 'PAGAMENTO_NO_PRAZO'
            when data_pagamento < data_vencimento_fatura then 'PAGAMENTO_ANTECIPADO'
            when data_pagamento > data_vencimento_fatura then 'PAGAMENTO_EM_ATRASO'
        end as fbc_classificacao_pagamento
    from df_join
""")
tb_classificacao_pagamento.createOrReplaceTempView('tb_classificacao_pagamento')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 33, Finished, Available, Finished)

In [32]:
tb_classificacao_pagamento.show(5)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 34, Finished, Available, Finished)

+----------+---------+-------------------+----------------------+------------+----------------------+------------+--------------+---------------+---------------------------+
|id_cliente|id_fatura|data_emissao_fatura|data_vencimento_fatura|valor_fatura|valor_pagamento_minimo|id_pagamento|data_pagamento|valor_pagamento|fbc_classificacao_pagamento|
+----------+---------+-------------------+----------------------+------------+----------------------+------------+--------------+---------------+---------------------------+
|         1|       11|         2023-01-01|            2023-01-10|    24597.21|               7379.16|          11|    2023-01-27|        8944.39|        PAGAMENTO_EM_ATRASO|
|         1|       12|         2023-02-01|            2023-02-10|    48891.09|              14667.33|          12|    2023-03-05|       16888.91|        PAGAMENTO_EM_ATRASO|
|         1|       13|         2023-03-01|            2023-03-10|    36954.04|              11086.21|        NULL|          NULL| 

In [33]:
# SEM_PAGAMENTO, PAGAMENTO_NO_PRAZO, PAGAMENTO_ANTECIPADO, PAGAMENTO_EM_ATRAZO

tb_dias_atraso = spark.sql("""
    select
        *,
        case
            when fbc_classificacao_pagamento = 'SEM_PAGAMENTO' then datediff("{dt_proc_book_str}",data_vencimento_fatura)
            when fbc_classificacao_pagamento = 'PAGAMENTO_EM_ATRASO' then datediff(data_pagamento, data_vencimento_fatura)
            when fbc_classificacao_pagamento = 'PAGAMENTO_NO_PRAZO' then 0
            when fbc_classificacao_pagamento = 'PAGAMENTO_ANTECIPADO' then -1
        end fvl_numero_dias_atraso
    from tb_classificacao_pagamento
""")
tb_dias_atraso.createOrReplaceTempView('tb_dias_atraso')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 35, Finished, Available, Finished)

In [ ]:
display(tb_dias_atraso)

In [35]:
# Percentual do pagamento da fatura

tb_percentual_pagamento = spark.sql("""
    SELECT
        *,
        ROUND((valor_pagamento/valor_fatura)*100, 2) as fvl_percentual_pagamento
    FROM tb_dias_atraso
""")
tb_percentual_pagamento.createOrReplaceTempView('tb_percentual_pagamento')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 37, Finished, Available, Finished)

In [36]:
# SEM_PAGAMENTO, PAGAMENTO_MINIMO, PAGAMENTO_MEDIO, PAGAMENTO_PARCIAL_TOTAL, PAGAMENTO_QUASE_TOTAL, PAGAMENTO_TOTAL

tb_status_pagamento = spark.sql("""
    SELECT
        *,
        CASE
            WHEN fvl_percentual_pagamento IS NULL THEN 'SEM_PAGAMENTO'
            WHEN fvl_percentual_pagamento <= 30.99 THEN 'PAGAMENTO_MINIMO'
            WHEN fvl_percentual_pagamento <= 60 THEN 'PAGAMENTO_MEDIO'
            WHEN fvl_percentual_pagamento <= 90 THEN 'PAGAMENTO_PARCIAL_TOTAL'
            WHEN fvl_percentual_pagamento <= 99.99 THEN 'PAGAMENTO_QUASE_TOTAL'
            ELSE 'PAGAMENTO_TOTAL'
        END AS fbc_status_perc_pagamento
    FROM tb_percentual_pagamento
""")
tb_status_pagamento.createOrReplaceTempView('tb_status_pagamento')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 38, Finished, Available, Finished)

In [ ]:
display(tb_status_pagamento)

In [40]:
# STAGE

stage = spark.sql(f"""
        SELECT
            id_cliente,
            SUBSTRING(REPLACE("{dt_proc_book_str}",'-',''),1,6) as ref,
            "{dt_proc}" as dt_proc,
            data_emissao_fatura,
            fbc_classificacao_pagamento,
            fvl_numero_dias_atraso,
            1 as fvl_qtd_transacao,
            fbc_status_perc_pagamento,
            fvl_percentual_pagamento,
            valor_fatura as fvl_valor_fatura
        FROM tb_status_pagamento
""")
stage.createOrReplaceTempView('stage')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 42, Finished, Available, Finished)

In [41]:
stage.printSchema()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 43, Finished, Available, Finished)

root
 |-- id_cliente: long (nullable = true)
 |-- ref: string (nullable = false)
 |-- dt_proc: string (nullable = false)
 |-- data_emissao_fatura: date (nullable = true)
 |-- fbc_classificacao_pagamento: string (nullable = true)
 |-- fvl_numero_dias_atraso: integer (nullable = true)
 |-- fvl_qtd_transacao: integer (nullable = false)
 |-- fbc_status_perc_pagamento: string (nullable = false)
 |-- fvl_percentual_pagamento: decimal(17,2) (nullable = true)
 |-- fvl_valor_fatura: decimal(10,2) (nullable = true)



In [43]:
stage.write.mode('append').partitionBy('ref').parquet("Files/Refined/stage_fatura")

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 45, Finished, Available, Finished)

**Book de Variáveis**

In [44]:
# Criação de Janela de Tempo dos últimos 1 mês, 3 meses, 6 meses, 9 meses, 12 meses

janelas_tempo = spark.sql(f"""
         SELECT
              *,
              "{dt_proc_book_str}",
              data_emissao_fatura,
              MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura),
              (CASE WHEN MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura) <= 1 THEN 1 ELSE 0 END) flg_u1m,
              (CASE WHEN MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura) <= 3 THEN 1 ELSE 0 END) flg_u3m,
              (CASE WHEN MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura) <= 6 THEN 1 ELSE 0 END) flg_u6m,
              (CASE WHEN MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura) <= 9 THEN 1 ELSE 0 END) flg_u9m,
              (CASE WHEN MONTHS_BETWEEN("{dt_proc_book_str}", data_emissao_fatura) <= 12 THEN 1 ELSE 0 END) flg_u12m
        FROM stage
""")
janelas_tempo.createOrReplaceTempView('janelas_tempo')

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 46, Finished, Available, Finished)

In [45]:
spark.sql("Select fbc_classificacao_pagamento FROM janelas_tempo GROUP BY 1").show()

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 47, Finished, Available, Finished)

+---------------------------+
|fbc_classificacao_pagamento|
+---------------------------+
|              SEM_PAGAMENTO|
|         PAGAMENTO_NO_PRAZO|
|        PAGAMENTO_EM_ATRASO|
|       PAGAMENTO_ANTECIPADO|
+---------------------------+



In [46]:
# Primeira Variável - Status Pagamento

fbc_00 = ['SEM_PAGAMENTO', 'PAGAMENTO_NO_PRAZO', 'PAGAMENTO_EM_ATRASO', 'PAGAMENTO_ANTECIPADO']
Fvls_00 = ['fvl_valor_fatura', 'fvl_numero_dias_atraso', 'fvl_qtd_transacao', 'fvl_percentual_pagamento']
janelas = ['flg_u1m', 'flg_u3m', 'flg_u6m', 'flg_u9m', 'flg_u12m']
aggs = ['SUM', 'AVG', 'MAX', 'MIN', 'COUNT']
count = 1

for fbc in fbc_00:
    for fvl in Fvls_00:
        for janela in janelas:
            for agg in aggs:
                if (fvl == 'fvl_numero_dias_atraso' and agg == 'SUM') or (fvl == 'fvl_qtd_transacao' and fvl != 'SUM'):
                    continue
                else:
                  print(f'{agg}(CASE WHEN fbc_classificacao_pagamento = "{fbc}" AND {janela} = 1 THEN {fvl} END) as VAR_{count}')
                  count += 1


StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 48, Finished, Available, Finished)

SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_1
AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_2
MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_3
MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_4
COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_5
SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_6
AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_7
MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_8
MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END)

In [47]:
# Segunda Variável - Porporção de Pagamento do Valor da Fatura

fbcs_01 = ['SEM_PAGAMENTO', 'PAGAMENTO_MINIMO', 'PAGAMENTO_MEDIO', 'PAGAMENTO_PARCIAL_TOTAL', 'PAGAMENTO_QUASE_TOTAL', 'PAGAMENTO_TOTAL']
Fvls_01 = ['fvl_valor_fatura', 'fvl_numero_dias_atraso', 'fvl_qtd_transacao', 'fvl_percentual_pagamento']
janelas = ['flg_u1m', 'flg_u3m', 'flg_u6m', 'flg_u9m', 'flg_u12m']
aggs = ['SUM', 'AVG', 'MAX', 'MIN', 'COUNT']
count = 1

for fbc in fbcs_01:
    for fvl in Fvls_01:
        for janela in janelas:
            for agg in aggs:
                if (fvl == 'fvl_numero_dias_atraso' and agg == 'SUM') or (fvl == 'fvl_qtd_transacao' and fvl != 'SUM'):
                    continue
                else:
                  print(f'{agg}(CASE WHEN fbc_status_perc_pagamento = "{fbc}" AND {janela} = 1 THEN {fvl} END) as VAR01_{count}')
                  count += 1


StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 49, Finished, Available, Finished)

SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_1
AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_2
MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_3
MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_4
COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_5
SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_6
AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_7
MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_8
MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) a

In [48]:
book = spark.sql("""
        SELECT
            id_cliente,
            ref,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_1,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_2,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_3,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_4,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_5,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_6,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_7,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_8,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_9,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_10,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_11,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_12,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_13,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_14,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_15,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_16,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_17,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_18,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_19,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_20,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_21,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_22,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_23,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_24,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_25,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_26,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_27,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_28,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_29,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_30,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_31,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_32,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_33,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_34,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_35,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_36,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_37,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_38,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_39,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_40,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_41,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_42,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_43,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_44,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_45,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_46,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_47,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_48,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_49,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_50,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_51,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_52,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_53,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_54,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_55,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_56,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_57,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_58,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_59,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_60,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_61,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_62,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_63,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_64,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_65,
            SUM(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_66,
            AVG(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_67,
            MAX(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_68,
            MIN(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_69,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_70,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_71,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_72,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_73,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_74,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_75,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_76,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_77,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_78,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_79,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_80,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_81,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_82,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_83,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_84,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_85,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_86,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_87,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_88,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_89,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_90,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_91,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_92,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_93,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_94,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_95,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_96,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_97,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_98,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_99,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_100,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_101,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_102,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_103,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_104,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_105,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_106,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_107,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_108,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_109,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_110,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_111,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_112,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_113,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_114,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_115,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_116,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_117,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_118,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_119,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_120,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_121,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_122,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_123,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_124,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_125,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_126,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_127,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_128,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_129,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_130,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_131,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_132,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_133,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_134,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_135,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_136,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_137,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_138,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_139,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_NO_PRAZO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_140,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_141,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_142,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_143,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_144,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_145,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_146,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_147,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_148,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_149,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_150,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_151,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_152,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_153,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_154,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_155,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_156,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_157,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_158,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_159,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_160,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_161,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_162,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_163,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_164,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_165,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_166,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_167,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_168,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_169,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_170,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_171,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_172,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_173,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_174,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_175,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_176,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_177,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_178,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_179,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_180,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_181,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_182,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_183,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_184,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_185,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_186,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_187,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_188,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_189,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_190,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_191,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_192,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_193,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_194,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_195,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_196,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_197,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_198,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_199,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_200,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_201,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_202,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_203,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_204,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_205,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_206,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_207,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_208,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_209,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_EM_ATRASO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_210,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_211,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_212,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_213,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_214,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR_215,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_216,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_217,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_218,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_219,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR_220,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_221,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_222,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_223,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_224,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR_225,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_226,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_227,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_228,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_229,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR_230,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_231,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_232,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_233,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_234,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR_235,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_236,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_237,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_238,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR_239,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_240,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_241,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_242,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR_243,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_244,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_245,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_246,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR_247,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_248,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_249,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_250,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR_251,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_252,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_253,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_254,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR_255,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_256,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_257,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_258,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_259,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR_260,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_261,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_262,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_263,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_264,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR_265,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_266,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_267,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_268,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_269,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR_270,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_271,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_272,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_273,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_274,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR_275,
            SUM(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_276,
            AVG(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_277,
            MAX(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_278,
            MIN(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_279,
            COUNT(CASE WHEN fbc_classificacao_pagamento = "PAGAMENTO_ANTECIPADO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR_280,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_1,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_2,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_3,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_4,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_5,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_6,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_7,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_8,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_9,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_10,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_11,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_12,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_13,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_14,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_15,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_16,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_17,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_18,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_19,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_20,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_21,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_22,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_23,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_24,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_25,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_26,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_27,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_28,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_29,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_30,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_31,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_32,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_33,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_34,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_35,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_36,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_37,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_38,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_39,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_40,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_41,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_42,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_43,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_44,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_45,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_46,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_47,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_48,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_49,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_50,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_51,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_52,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_53,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_54,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_55,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_56,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_57,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_58,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_59,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_60,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_61,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_62,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_63,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_64,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_65,
            SUM(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_66,
            AVG(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_67,
            MAX(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_68,
            MIN(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_69,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "SEM_PAGAMENTO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_70,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_71,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_72,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_73,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_74,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_75,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_76,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_77,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_78,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_79,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_80,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_81,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_82,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_83,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_84,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_85,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_86,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_87,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_88,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_89,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_90,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_91,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_92,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_93,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_94,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_95,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_96,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_97,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_98,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_99,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_100,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_101,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_102,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_103,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_104,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_105,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_106,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_107,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_108,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_109,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_110,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_111,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_112,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_113,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_114,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_115,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_116,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_117,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_118,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_119,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_120,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_121,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_122,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_123,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_124,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_125,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_126,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_127,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_128,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_129,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_130,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_131,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_132,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_133,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_134,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_135,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_136,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_137,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_138,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_139,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MINIMO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_140,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_141,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_142,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_143,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_144,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_145,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_146,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_147,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_148,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_149,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_150,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_151,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_152,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_153,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_154,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_155,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_156,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_157,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_158,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_159,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_160,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_161,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_162,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_163,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_164,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_165,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_166,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_167,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_168,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_169,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_170,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_171,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_172,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_173,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_174,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_175,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_176,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_177,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_178,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_179,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_180,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_181,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_182,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_183,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_184,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_185,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_186,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_187,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_188,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_189,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_190,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_191,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_192,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_193,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_194,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_195,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_196,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_197,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_198,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_199,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_200,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_201,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_202,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_203,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_204,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_205,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_206,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_207,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_208,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_209,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_MEDIO" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_210,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_211,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_212,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_213,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_214,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_215,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_216,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_217,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_218,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_219,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_220,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_221,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_222,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_223,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_224,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_225,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_226,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_227,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_228,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_229,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_230,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_231,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_232,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_233,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_234,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_235,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_236,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_237,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_238,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_239,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_240,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_241,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_242,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_243,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_244,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_245,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_246,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_247,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_248,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_249,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_250,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_251,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_252,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_253,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_254,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_255,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_256,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_257,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_258,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_259,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_260,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_261,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_262,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_263,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_264,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_265,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_266,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_267,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_268,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_269,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_270,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_271,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_272,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_273,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_274,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_275,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_276,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_277,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_278,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_279,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_PARCIAL_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_280,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_281,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_282,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_283,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_284,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_285,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_286,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_287,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_288,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_289,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_290,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_291,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_292,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_293,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_294,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_295,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_296,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_297,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_298,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_299,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_300,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_301,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_302,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_303,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_304,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_305,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_306,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_307,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_308,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_309,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_310,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_311,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_312,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_313,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_314,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_315,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_316,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_317,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_318,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_319,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_320,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_321,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_322,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_323,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_324,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_325,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_326,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_327,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_328,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_329,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_330,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_331,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_332,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_333,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_334,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_335,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_336,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_337,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_338,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_339,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_340,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_341,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_342,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_343,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_344,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_345,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_346,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_347,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_348,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_349,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_QUASE_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_350,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_351,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_352,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_353,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_354,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_valor_fatura END) as VAR01_355,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_356,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_357,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_358,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_359,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_valor_fatura END) as VAR01_360,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_361,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_362,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_363,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_364,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_valor_fatura END) as VAR01_365,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_366,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_367,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_368,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_369,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_valor_fatura END) as VAR01_370,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_371,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_372,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_373,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_374,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_valor_fatura END) as VAR01_375,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_376,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_377,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_378,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_numero_dias_atraso END) as VAR01_379,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_380,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_381,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_382,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_numero_dias_atraso END) as VAR01_383,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_384,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_385,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_386,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_numero_dias_atraso END) as VAR01_387,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_388,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_389,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_390,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_numero_dias_atraso END) as VAR01_391,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_392,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_393,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_394,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_numero_dias_atraso END) as VAR01_395,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_396,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_397,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_398,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_399,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u1m = 1 THEN fvl_percentual_pagamento END) as VAR01_400,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_401,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_402,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_403,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_404,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u3m = 1 THEN fvl_percentual_pagamento END) as VAR01_405,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_406,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_407,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_408,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_409,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u6m = 1 THEN fvl_percentual_pagamento END) as VAR01_410,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_411,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_412,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_413,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_414,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u9m = 1 THEN fvl_percentual_pagamento END) as VAR01_415,
            SUM(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_416,
            AVG(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_417,
            MAX(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_418,
            MIN(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_419,
            COUNT(CASE WHEN fbc_status_perc_pagamento = "PAGAMENTO_TOTAL" AND flg_u12m = 1 THEN fvl_percentual_pagamento END) as VAR01_420
      FROM janelas_tempo
      GROUP BY 1,2
""")

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 50, Finished, Available, Finished)

In [50]:
display(book)

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 52, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 6505b1ae-96ef-4a5f-9fe9-3e2bfc51ccb2)

In [51]:
# Salvando Book de Variáveis

book.write.mode('append').partitionBy('ref').parquet("Files/Refined/book_fatura")

StatementMeta(, 8932c5c4-b075-42a0-b482-e140593b704f, 53, Finished, Available, Finished)